In [1]:
import matplotlib.pyplot as plt
import plotly.express as px
import numpy as np
import pandas as pd
import inflect
import plotly.io as pio
import random
p = inflect.engine()





In [2]:
indices_to_plot = random.sample(range(0, 2000 ), 100)

In [20]:
num_nodes = [50,100,500,1000]
num_com = 4
num_samples = 2000
min_comm_prob = 0.0
max_comm_prob = 0.5
uniform_node_comm_assignment = False
degree_naive = False
noise_gaussian_std = 0.05
random_seed = 42
multiplicity_model = 1
recall_rejection_cutoff = 0

result_folder = '../results/vs_dedi_paper_params/'

In [21]:
import itertools

##load n2v2r 

list_all_n2v2r_non_binary = []
list_all_n2v2r_binary = []
list_all_n2v2r_recall = []

list_all_n2v2r_borda_non_binary = []
list_all_n2v2r_borda_binary = []
list_all_n2v2r_borda_recall = []

list_all_absDeDi_non_binary = []
list_all_absDeDi_binary = []
list_all_absDeDi_recall = []



for num in num_nodes:

    par_configuration = str(num) +"_"+ str(num_com) + "_" + str(num_samples) + "_" + str(min_comm_prob) + "_" + str(max_comm_prob) + "_"+ "sampleuni-"+str(uniform_node_comm_assignment)  + "__degn-"+ str(degree_naive) +"_noisestd-"+str(noise_gaussian_std)

    #load n2v2r
    result_fn = result_folder+par_configuration+"/n2v2r_non_binary_scores.csv"
    result_np = np.loadtxt(result_fn)
    list_all_n2v2r_non_binary.append(result_np)

    result_fn = result_folder+par_configuration+"/n2v2r_binary_scores.csv"
    result_np = np.loadtxt(result_fn)
    list_all_n2v2r_binary.append(result_np)

    result_fn = result_folder+par_configuration+"/n2v2r_recalls.csv"
    result_np = np.loadtxt(result_fn)
    list_all_n2v2r_recall.append(result_np)

    #load n2v2r_borda
    result_fn = result_folder+par_configuration+"/n2v2r_borda_non_binary_scores.csv"
    result_np = np.loadtxt(result_fn)
    list_all_n2v2r_borda_non_binary.append(result_np)

    result_fn = result_folder+par_configuration+"/n2v2r_borda_binary_scores.csv"
    result_np = np.loadtxt(result_fn)
    list_all_n2v2r_borda_binary.append(result_np)

    result_fn = result_folder+par_configuration+"/n2v2r_borda_recalls.csv"
    result_np = np.loadtxt(result_fn)
    list_all_n2v2r_borda_recall.append(result_np)


    #load absDeDi
    result_fn = result_folder+par_configuration+"/absDeDi_non_binary_scores.csv"
    result_np = np.loadtxt(result_fn)
    list_all_absDeDi_non_binary.append(result_np)

    result_fn = result_folder+par_configuration+"/absDeDi_binary_scores.csv"
    result_np = np.loadtxt(result_fn)
    list_all_absDeDi_binary.append(result_np)

    result_fn = result_folder+par_configuration+"/absDeDi_recalls.csv"
    result_np = np.loadtxt(result_fn)
    list_all_absDeDi_recall.append(result_np)

In [14]:
for i in range(len(num_nodes)):
    ndcgs = np.concatenate((list_all_n2v2r_borda_binary[i],list_all_absDeDi_binary[i]), axis=None)
    num_models = len(list_all_n2v2r_non_binary[i])

    method_indicator = (['n2v2r'] * ((num_com)*num_models)) +  (['DeDi'] * ((num_com)*num_models))
    comms = [p.ordinal(i) for i in range(1,num_com+1)]

    comms_indicator = (comms * 2)*num_models

    df = pd.DataFrame(list(zip(ndcgs,  method_indicator, comms_indicator)),
                columns =['ndcgs', 'method', 'most changing communities'])

    df = df[(df['most changing communities']=='1st')]



    fig = px.violin(df, y="ndcgs", x="method", color="method", box=True, points=False,
                hover_data=df.columns, color_discrete_sequence=["green",  "#7570b3"])

    fig.update_traces(meanline_visible=True, spanmode='hard',
                        box_visible=True)
    fig.update_layout( title=f'{num_nodes[i]} nodes in {num_com} communities',
    xaxis_title="ordered communities",
    yaxis_title="ndcg",
    legend_title="Method",width=600,
    height=400)
    
    fig.update_layout(xaxis_title=None)


    
    fig.update_layout(showlegend=False)


    # Add lines connecting corresponding points
    indices_to_plot = random.sample(range(0, len(list_all_n2v2r_borda_binary[i][:,0]) ), 100)

    [fig.add_shape(type="line", x0=0.06, y0=list_all_n2v2r_borda_binary[i][j,0], x1=0.94, y1=list_all_absDeDi_binary[i][j,0], line=dict(color="gray", width=0.5, dash="dot")) for j in indices_to_plot]

    fig.show()

    # fig.write_image(result_folder+"/"+ f'{num_nodes[i]}-nodes_{num_com}-com_degNaive-{degree_naive}_uniform-{uniform_node_comm_assignment}_ndcg.pdf')


In [22]:
for i in range(len(num_nodes)):
    recalls = np.concatenate((list_all_n2v2r_borda_recall[i],list_all_n2v2r_recall[i],list_all_absDeDi_recall[i]), axis=None)
    num_models = len(list_all_n2v2r_recall[i])

    method_indicator = (['n2v2r'] * ((num_com)*num_models)) + (['DeDi'] * ((num_com)*num_models))
    comms = [p.ordinal(i) for i in range(1,num_com+1)]

    comms_indicator = (comms * 2)*num_models

    df = pd.DataFrame(list(zip(recalls,  method_indicator, comms_indicator)),
                columns =['recalls', 'method', 'most changing communities'])

    df = df[(df['most changing communities']=='1st')]



    fig = px.violin(df, y="recalls", x="method", color="method", box=True, points=False,
                hover_data=df.columns, color_discrete_sequence=["green", "#7570b3"])

    fig.update_traces(meanline_visible=True, spanmode='hard',
                        box_visible=True)
    fig.update_layout( title=f'{num_nodes[i]} nodes in {num_com} communities',
        xaxis_title="ordered communities",
    yaxis_title="recall",
    legend_title="Method",width=600,
    height=400)
    
    fig.update_layout(xaxis_title=None)

    if num_nodes[i]/num_com > num_com:
        fig.add_hline(y=((num_nodes[i]/num_com)/num_com)/(num_nodes[i]/num_com), line_width=2, line_dash="dash", line_color="black")

    fig.update_layout(showlegend=False)
        

    [fig.add_shape(type="line", x0=0.06, y0=list_all_n2v2r_borda_recall[i][j,0], x1=0.94, y1=list_all_absDeDi_recall[i][j,0], line=dict(color="gray", width=0.5, dash="dot")) for j in indices_to_plot]


    fig.show()
    fig.write_image(result_folder+"/"+ f'{num_nodes[i]}-nodes_{num_com}-com_degNaive-{degree_naive}_uniform-{uniform_node_comm_assignment}_recall_vsDeDi.pdf')
